Try
- sample weighting
- different objectives

In [1]:
import numpy as np
import pandas as pd
from xgboost import XGBRegressor
import optuna
from sklearn.metrics import r2_score, mean_squared_error, mean_absolute_error

import matplotlib.pyplot as plt
import plotly.graph_objects as go

pd.set_option('display.max_columns', 501)
pd.set_option('display.max_rows', 501)

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/compat.py:36: FutureWarning: pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  from pandas import MultiIndex, Int64Index


# FUNCTIONS

In [2]:
# hyper-paremeter optimization
def optimize(n_optimization_trials, training_X, training_y, validation_X, validation_y):

    study = optuna.create_study()
    study.optimize(objective, n_trials=n_optimization_trials)
    print('Best params:')
    print(study.best_params)
    print('RMSE for best params:')
    print(study.best_value)

In [62]:
def train_model(xgb_params, fit_params, training_X, training_y, validation_X, validation_y, testing_X, testing_y):

    # fit model
    model = XGBRegressor(**xgb_params)
    model.fit(training_X, training_y, eval_set=[(validation_X, validation_y)], **fit_params)

    # metrics
    predictions_validation = model.predict(validation_X)
    rmse_validation = mean_squared_error(validation_y, predictions_validation, squared=False)
    mae_validation = mean_absolute_error(validation_y, predictions_validation)
    r2_validation = r2_score(validation_y, predictions_validation)
    print(f'Validation RMSE: {rmse_validation}')
    print(f'Validation MAE: {mae_validation}')
    print(f'Validation R2: {r2_validation}')
    predictions_test = model.predict(testing_X)
    rmse_test = mean_squared_error(testing_y, predictions_test, squared=False)
    mae_test = mean_absolute_error(testing_y, predictions_test)
    r2_test = r2_score(testing_y, predictions_test)
    print(f'Test RMSE: {rmse_test}')
    print(f'Test MAE: {mae_test}')
    print(f'Test R2: {r2_test}')
    
    return model

In [4]:
def draw_player_predictions(name_string, testing_full, model):
    
    aux = testing_full[testing_full['name'].str.contains(name_string)]
    y_true = aux['total_points']
    xPoints = aux['xPoints']
    y_pred = model.predict(aux[input_variables])

    fig = go.Figure()

    fig.add_trace(
        go.Scatter(
            x=aux['GW'],
            y=y_true,
           mode="markers+lines",
            name='true points'
        )
    )

    fig.add_trace(
        go.Scatter(
            x=aux['GW'],
            y=xPoints,
           mode="markers+lines",
            name='xPoints'
        )
    )

    fig.add_trace(
        go.Scatter(
            x=aux['GW'],
            y=y_pred,
           mode="markers+lines",
            name='predicted points'
        )
    )

    #fig.update_xaxes(range=[predictions.min()-1, predictions.max()+1])

    fig.update_layout(
        title=aux['name'].unique()[0],
        xaxis_title="gameweek",
        yaxis_title="points",
        showlegend=True
        )

    fig.show()

    print(f'Total true points: {np.sum(y_true)}')
    print(f'Total expected points: {np.sum(xPoints)}')
    print(f'Total predicted points: {np.sum(y_pred)}')

In [41]:
def calculate_all_player_predictions(testing_full, model):
    
    player_names = testing_full['name'].unique()
    stats = []
    for player_name in player_names:
        aux = testing_full[testing_full['name']==player_name]
        total_points = aux['total_points'].sum()
        xPoints = aux['xPoints'].sum()
        predicted_points = model.predict(aux[input_variables]).sum()
        stats.append((player_name, total_points, xPoints, predicted_points))

    stats_df = pd.DataFrame(data=stats, columns=['name', 'total_points', 'xPoints', 'predicted_points'])
    
    return stats_df

In [42]:
def draw_all_predictions(stats_df):
    
    

    fig = go.Figure()

    fig.add_trace(
        go.Scatter(
            x=stats_df['predicted_points'],
            y=stats_df['total_points'],
            hovertext=stats_df['name'],
           mode="markers",
            #opacity=0.6,
        )
    )

    fig.add_trace(
        go.Scatter(
            x=np.linspace(0,250,100),
            y=np.linspace(0,250,100),
           mode="lines",
        )
    )

    #fig.update_xaxes(range=[predictions_test.min()-1, predictions_test.max()+1])

    fig.update_layout(
        title="Test set",
        xaxis_title="predicted points",
        yaxis_title="true points",
        showlegend=False
        )

    fig.show()

# DATA

In [6]:
data = pd.read_csv('../../data/data_for_modelling.csv', index_col=0)
data

season                  name position  assists  bonus  bps  \
0      2017-18       Aaron Cresswell      DEF        0      0    3   
1752   2017-18       Aaron Cresswell      DEF        0      0   16   
3513   2017-18       Aaron Cresswell      DEF        0      0   11   
5141   2017-18       Aaron Cresswell      DEF        0      0   23   
5295   2017-18       Aaron Cresswell      DEF        0      3   30   
...        ...                   ...      ...      ...    ...  ...   
40554  2021-22        Tony Springett      MID        0      0    2   
40555  2021-22        Tony Springett      MID        0      0    9   
40921  2021-22        Tony Springett      MID        0      0    0   
40851  2021-22  Nathan Young-Coombes      FWD        0      0    2   
40970  2021-22           Isaac Price      MID        0      0   -2   

       clean_sheets  creativity  element  fixture  goals_conceded  \
0                 0         0.6      443        9               2   
1752              0        52.9      443       15               3   
3513              0         1.6      443       26               3   
5141              1        47.1      443       40               0   
5295              1        34.3      443       48               0   
...             ...         ...      ...      ...             ...   
40554             0         0.7      716      360               1   
40555             0        21.0      716      207               2   
40921             0         0.0      716      380               3   
40851             0         0.0      640      352               0   
40970             0         0.0      718      371               1   

       goals_scored  ict_index  influence               kickoff_time  minutes  \
0                 0        1.9        0.4  2017-08-13 15:00:00+00:00        9   
1752              0        7.4       21.2  2017-08-19 14:00:00+00:00       90   
3513              0        2.4       11.2  2017-08-26 14:00:00+00:00       90   
5141              0        6.2       14.2  2017-09-11 19:00:00+00:00       90   
5295              0        4.6       11.2  2017-09-16 14:00:00+00:00       90   
...             ...        ...        ...                        ...      ...   
40554             0        1.0        1.4  2022-05-08 13:00:00+00:00       45   
40555             0        5.3       13.0  2022-05-11 18:45:00+00:00       66   
40921             0        0.0        0.0  2022-05-22 15:00:00+00:00       29   
40851             0        0.0        0.0  2022-05-07 14:00:00+00:00        3   
40970             0        0.0        0.0  2022-05-22 15:00:00+00:00       13   

       opponent_team   opp_team_name  own_goals  penalties_missed  \
0                 12  Manchester Utd          0                 0   
1752              14     Southampton          0                 0   
3513              13   Newcastle Utd          0                 0   
5141               8    Huddersfield          0                 0   
5295              19       West Brom          0                 0   
...              ...             ...        ...               ...   
40554             19        West Ham          0                 0   
40555              9  Leicester City          0                 0   
40921             17       Tottenham          0                 0   
40851             16     Southampton          0                 0   
40970              1         Arsenal          0                 0   

       penalties_saved  red_cards  round  saves  selected  team_a_score  \
0                    0          0      1      0       NaN           0.0   
1752                 0          0      2      0   25136.0           2.0   
3513                 0          0      3      0   27824.0           0.0   
5141                 0          0      4      0   28464.0           0.0   
5295                 0          0      5      0   28977.0           0.0   
...                ...        ...    ...    ...       ...           ...   
40554      

In [7]:
training_full = data[(data['season']=='2017-18') | (data['season']=='2018-19') | (data['season']=='2019-20')].copy()
validation_full = data[(data['season']=='2020-21')].copy()
testing_full = data[(data['season']=='2021-22')].copy()
display(training_full)
display(validation_full)
display(testing_full)

season             name position  assists  bonus  bps  clean_sheets  \
0      2017-18  Aaron Cresswell      DEF        0      0    3             0   
1752   2017-18  Aaron Cresswell      DEF        0      0   16             0   
3513   2017-18  Aaron Cresswell      DEF        0      0   11             0   
5141   2017-18  Aaron Cresswell      DEF        0      0   23             1   
5295   2017-18  Aaron Cresswell      DEF        0      3   30             1   
...        ...              ...      ...      ...    ...  ...           ...   
21549  2019-20      Jake Vokins      DEF        0      0   10             0   
21597  2019-20      Luke Thomas      DEF        1      3   37             1   
21845  2019-20      Luke Thomas      DEF        0      0   16             0   
22088  2019-20      Luke Thomas      DEF        0      0   17             0   
22072  2019-20    Kelland Watts      DEF        0      0    3             0   

       creativity  element  fixture  goals_conceded  goals_scored  ict_index  \
0             0.6      443        9               2             0        1.9   
1752         52.9      443       15               3             0        7.4   
3513          1.6      443       26               3             0        2.4   
5141         47.1      443       40               0             0        6.2   
5295         34.3      443       48               0             0        4.6   
...           ...      ...      ...             ...           ...        ...   
21549        16.7      645      359               1             0        2.8   
21597        39.1      660      356               0             0        7.8   
21845        52.9      660      368               3             0        7.9   
22088        57.8      660      376               1             0        8.2   
22072         0.0      599      378               1             0        0.2   

       influence               kickoff_time  minutes  opponent_team  \
0            0.4  2017-08-13 15:00:00+00:00        9             12   
1752        21.2  2017-08-19 14:00:00+00:00       90             14   
3513        11.2  2017-08-26 14:00:00+00:00       90             13   
5141        14.2  2017-09-11 19:00:00+00:00       90              8   
5295        11.2  2017-09-16 14:00:00+00:00       90             19   
...          ...                        ...      ...            ...   
21549        8.4  2020-07-16 19:15:00+00:00       90              4   
21597       36.4  2020-07-16 17:00:00+00:00       90             15   
21845       20.0  2020-07-19 15:00:00+00:00       90             17   
22088       22.0  2020-07-26 15:00:00+00:00       87             12   
22072        2.0  2020-07-26 15:00:00+00:00       16             10   

        opp_team_name  own_goals  penalties_missed  penalties_saved  \
0      Manchester Utd          0                 0                0   
1752      Southampton          0                 0                0   
3513    Newcastle Utd          0                 0                0   
5141     Huddersfield          0                 0                0   
5295        West Brom          0                 0                0   
...               ...        ...               ...              ...   
21549        Brighton          0                 0                0   
21597   Sheffield Utd          0                 0                0   
21845       Tottenham          0                 0                0   
22088  Manchester Utd          0                 0                0   
22072       Liverpool          0                 0                0   

       red_cards  round  saves  selected  team_a_score  team_h_score  threat  \
0              0      1      0       NaN           0.0           4.0    18.0   
1752           0      2      0   25136.0           2.0           3.0     0.0   
3513           0      3      0   27824.0           0.0           3.0    11.0   
5141           0      4      0   28464.0           0.0           2.0    

season                name position  assists  bonus  bps  \
22189  2020-21     Aaron Cresswell      DEF        0      0   11   
22390  2020-21     Aaron Cresswell      DEF        0      0   17   
22642  2020-21     Aaron Cresswell      DEF        0      1   32   
22889  2020-21     Aaron Cresswell      DEF        2      3   57   
23137  2020-21     Aaron Cresswell      DEF        1      1   27   
...        ...                 ...      ...      ...    ...  ...   
31594  2020-21     Gaetano Berardi      DEF        0      1   25   
31456  2020-21  Carney Chukwuemeka      MID        0      0    3   
31714  2020-21  Carney Chukwuemeka      MID        0      0    4   
31510  2020-21     Hannibal Mejbri      MID        0      0    2   
31530  2020-21     Tyrese Francois      MID        0      0    2   

       clean_sheets  creativity  element  fixture  goals_conceded  \
22189             0        11.2      435        6               2   
22390             0        35.0      435        9               2   
22642             1        52.5      435       28               0   
22889             1        52.5      435       34               0   
23137             0        34.0      435       47               3   
...             ...         ...      ...      ...             ...   
31594             1         0.8      685      372               0   
31456             0         0.8      672      367               0   
31714             0         0.3      672      370               0   
31510             0         0.0      712      378               0   
31530             0         1.3      708      371               1   

       goals_scored  ict_index  influence               kickoff_time  minutes  \
22189             0        2.2       10.4  2020-09-12 19:00:00+00:00       90   
22390             0        6.2       27.0  2020-09-19 19:00:00+00:00       90   
22642             0        8.8       35.8  2020-09-27 18:00:00+00:00       90   
22889             0       10.5       52.8  2020-10-04 11:00:00+00:00       90   
23137             0        6.8       32.6  2020-10-18 15:30:00+00:00       90   
...             ...        ...        ...                        ...      ...   
31594             0        3.2       13.4  2021-05-23 15:00:00+00:00       68   
31456             0        0.3        0.0  2021-05-19 17:00:00+00:00        1   
31714             0        0.3        1.0  2021-05-23 15:00:00+00:00       17   
31510             0        0.1        1.2  2021-05-23 15:00:00+00:00        8   
31530             0        0.3        1.2  2021-05-23 15:00:00+00:00       14   

       opponent_team   opp_team_name  own_goals  penalties_missed  \
22189             14   Newcastle Utd          0                 0   
22390              1         Arsenal          0                 0   
22642             20          Wolves          0                 0   
22889              9  Leicester City          0                 0   
23137             17       Tottenham          0                 0   
...              ...             ...        ...               ...   
31594             18       West Brom          0                 0   
31456             17       Tottenham          0                 0   
31714              5         Chelsea          0                 0   
31510             20          Wolves          0                 0   
31530             14   Newcastle Utd          0                 0   

       penalties_saved  red_cards  round  saves  selected  team_a_score  \
22189                0          0      1      0  121786.0           2.0   
22390                0          0      2      0   70232.0           1.0   
22642                0          0      3      0   62831.0           0.0   
22889                0          0      4      0   58281.0           3.0   
23137                0          0      5      0   61303.0           3.0   
...                ...        ...    ...    ...       ...           ...   
31594                0          0  

season                  name position  assists  bonus  bps  \
31978  2021-22       Aaron Cresswell      DEF        0      0   30   
32236  2021-22       Aaron Cresswell      DEF        0      0   12   
32489  2021-22       Aaron Cresswell      DEF        1      1   26   
32747  2021-22       Aaron Cresswell      DEF        0      2   27   
33003  2021-22       Aaron Cresswell      DEF        0      0   15   
...        ...                   ...      ...      ...    ...  ...   
40554  2021-22        Tony Springett      MID        0      0    2   
40555  2021-22        Tony Springett      MID        0      0    9   
40921  2021-22        Tony Springett      MID        0      0    0   
40851  2021-22  Nathan Young-Coombes      FWD        0      0    2   
40970  2021-22           Isaac Price      MID        0      0   -2   

       clean_sheets  creativity  element  fixture  goals_conceded  \
31978             0        17.5      411        9               2   
32236             0         4.2      411       20               1   
32489             0        17.2      411       28               2   
32747             1        24.6      411       39               0   
33003             0        27.3      411       49               2   
...             ...         ...      ...      ...             ...   
40554             0         0.7      716      360               1   
40555             0        21.0      716      207               2   
40921             0         0.0      716      380               3   
40851             0         0.0      640      352               0   
40970             0         0.0      718      371               1   

       goals_scored  ict_index  influence               kickoff_time  minutes  \
31978             1        9.1       55.8  2021-08-15 13:00:00+00:00       90   
32236             0        1.9        8.6  2021-08-23 19:00:00+00:00       90   
32489             0        3.9       20.2  2021-08-28 14:00:00+00:00       90   
32747             0        4.4       10.0  2021-09-11 14:00:00+00:00       90   
33003             0        4.3       15.4  2021-09-19 13:00:00+00:00       90   
...             ...        ...        ...                        ...      ...   
40554             0        1.0        1.4  2022-05-08 13:00:00+00:00       45   
40555             0        5.3       13.0  2022-05-11 18:45:00+00:00       66   
40921             0        0.0        0.0  2022-05-22 15:00:00+00:00       29   
40851             0        0.0        0.0  2022-05-07 14:00:00+00:00        3   
40970             0        0.0        0.0  2022-05-22 15:00:00+00:00       13   

       opponent_team   opp_team_name  own_goals  penalties_missed  \
31978             14   Newcastle Utd          0                 0   
32236              9  Leicester City          0                 0   
32489              7  Crystal Palace          0                 0   
32747             16     Southampton          0                 0   
33003             13  Manchester Utd          0                 0   
...              ...             ...        ...               ...   
40554             19        West Ham          0                 0   
40555              9  Leicester City          0                 0   
40921             17       Tottenham          0                 0   
40851             16     Southampton          0                 0   
40970              1         Arsenal          0                 0   

       penalties_saved  red_cards  round  saves   selected  team_a_score  \
31978                0          0      1      0  1504350.0           4.0   
32236                0          0      2      0  1213434.0           1.0   
32489                0          0      3      0  1345295.0           2.0   
32747                0          0      4      0  1402594.0           0.0   
33003                0          0      5      0  1324980.0           2.0   
...                ...        ...    ...    ...        ...           ...   
4055

In [8]:
# declare all variables that will go into the model
target = 'total_points'
input_variables = ['fpl_position_GK', 'fpl_position_DEF', 'fpl_position_MID', 'fpl_position_FWD',
       'fbref_position_GK', 'fbref_position_LB', 'fbref_position_CB',
       'fbref_position_RB', 'fbref_position_WB', 'fbref_position_DM',
       'fbref_position_LM', 'fbref_position_CM', 'fbref_position_RM',
       'fbref_position_AM', 'fbref_position_LW', 'fbref_position_RW',
       'fbref_position_FW', 'team_xG_ewa_5_shifted', 'team_xG_ewa_10_shifted',
       'team_xG_ewa_20_shifted', 'team_xG_ewa_40_shifted',
       'team_xGA_ewa_5_shifted', 'team_xGA_ewa_10_shifted',
       'team_xGA_ewa_20_shifted', 'team_xGA_ewa_40_shifted', 'opp_team_xG_ewa_5_shifted',
       'opp_team_xG_ewa_10_shifted', 'opp_team_xG_ewa_20_shifted',
       'opp_team_xG_ewa_40_shifted', 'opp_team_xGA_ewa_5_shifted',
       'opp_team_xGA_ewa_10_shifted', 'opp_team_xGA_ewa_20_shifted',
       'opp_team_xGA_ewa_40_shifted', 'games_in_past_5_days',
       'games_in_past_10_days', 'games_in_past_20_days', 'games_in_past_40_days',
        'transfers_balance_%', 'transfers_balance_%_ewa5', 'transfers_balance_%_ewa10',
        'value_change_1', 'value_change_2', 'value_change_5',
       'total_points_ewa_5', 'xPoints_ewa_5', 'assists_ewa_5',
       'bonus_ewa_5', 'bps_ewa_5', 'clean_sheets_ewa_5',
       'creativity_ewa_5', 'goals_conceded_ewa_5', 'goals_scored_ewa_5',
       'ict_index_ewa_5', 'influence_ewa_5', 'minutes_ewa_5',
       'own_goals_ewa_5', 'penalties_missed_ewa_5',
       'penalties_saved_ewa_5', 'saves_ewa_5', 'threat_ewa_5',
       'yellow_cards_ewa_5', 'Performance_Sh_ewa_5',
       'Performance_SoT_ewa_5', 'Performance_Touches_ewa_5',
       'Performance_Press_ewa_5', 'Performance_Tkl_ewa_5',
       'Performance_Int_ewa_5', 'Performance_Blocks_ewa_5',
       'Expected_xG_ewa_5', 'Expected_npxG_ewa_5', 'Expected_xA_ewa_5',
       'SCA_SCA_ewa_5', 'Passes_Cmp_ewa_5', 'Passes_Cmp%_ewa_5',
       'Passes_Prog_ewa_5', 'Carries_Carries_ewa_5', 'Carries_Prog_ewa_5',
       'Dribbles_Succ_ewa_5', 'Dribbles_Att_ewa_5', 'General_KP_ewa_5',
       'Touches_Att 3rd_ewa_5', 'Touches_Att Pen_ewa_5',
       'Performance_Recov_ewa_5', 'Aerial Duels_Won_ewa_5',
       'Aerial Duels_Won%_ewa_5', 'total_points_ewa_10', 'xPoints_ewa_10',
       'assists_ewa_10', 'bonus_ewa_10', 'bps_ewa_10',
       'clean_sheets_ewa_10', 'creativity_ewa_10',
       'goals_conceded_ewa_10', 'goals_scored_ewa_10', 'ict_index_ewa_10',
       'influence_ewa_10', 'minutes_ewa_10', 'own_goals_ewa_10',
       'penalties_missed_ewa_10', 'penalties_saved_ewa_10',
       'saves_ewa_10', 'threat_ewa_10', 'yellow_cards_ewa_10',
       'Performance_Sh_ewa_10', 'Performance_SoT_ewa_10',
       'Performance_Touches_ewa_10', 'Performance_Press_ewa_10',
       'Performance_Tkl_ewa_10', 'Performance_Int_ewa_10',
       'Performance_Blocks_ewa_10', 'Expected_xG_ewa_10',
       'Expected_npxG_ewa_10', 'Expected_xA_ewa_10', 'SCA_SCA_ewa_10',
       'Passes_Cmp_ewa_10', 'Passes_Cmp%_ewa_10', 'Passes_Prog_ewa_10',
       'Carries_Carries_ewa_10', 'Carries_Prog_ewa_10',
       'Dribbles_Succ_ewa_10', 'Dribbles_Att_ewa_10', 'General_KP_ewa_10',
       'Touches_Att 3rd_ewa_10', 'Touches_Att Pen_ewa_10',
       'Performance_Recov_ewa_10', 'Aerial Duels_Won_ewa_10',
       'Aerial Duels_Won%_ewa_10', 'total_points_ewa_20',
       'xPoints_ewa_20', 'assists_ewa_20', 'bonus_ewa_20', 'bps_ewa_20',
       'clean_sheets_ewa_20', 'creativity_ewa_20',
       'goals_conceded_ewa_20', 'goals_scored_ewa_20', 'ict_index_ewa_20',
       'influence_ewa_20', 'minutes_ewa_20', 'own_goals_ewa_20',
       'penalties_missed_ewa_20', 'penalties_saved_ewa_20',
       'saves_ewa_20', 'threat_ewa_20', 'yellow_cards_ewa_20',
       'Performance_Sh_ewa_20', 'Performance_SoT_ewa_20',
       'Performance_Touches_ewa_20', 'Performance_Press_ewa_20',
       'Performance_Tkl_ewa_20', 'Performance_Int_ewa_20',
       'Performance_Blocks_ewa_20', 'Expected_xG_ewa_20',
       'Expected_npxG_ewa_20', 'Expected_xA_ewa_20', 'SCA_SCA_ewa_20',
       'Passes_Cmp_ewa_20', 'Passes_Cmp%_ewa_20', 'Passes_Prog_ewa_20',
       'Carries_Carries_ewa_20', 'Carries_Prog_ewa_20',
       'Dribbles_Succ_ewa_20', 'Dribbles_Att_ewa_20', 'General_KP_ewa_20',
       'Touches_Att 3rd_ewa_20', 'Touches_Att Pen_ewa_20',
       'Performance_Recov_ewa_20', 'Aerial Duels_Won_ewa_20',
       'Aerial Duels_Won%_ewa_20', 'total_points_ewa_40',
       'xPoints_ewa_40', 'assists_ewa_40', 'bonus_ewa_40', 'bps_ewa_40',
       'clean_sheets_ewa_40', 'creativity_ewa_40',
       'goals_conceded_ewa_40', 'goals_scored_ewa_40', 'ict_index_ewa_40',
       'influence_ewa_40', 'minutes_ewa_40', 'own_goals_ewa_40',
       'penalties_missed_ewa_40', 'penalties_saved_ewa_40',
       'saves_ewa_40', 'threat_ewa_40', 'yellow_cards_ewa_40',
       'Performance_Sh_ewa_40', 'Performance_SoT_ewa_40',
       'Performance_Touches_ewa_40', 'Performance_Press_ewa_40',
       'Performance_Tkl_ewa_40', 'Performance_Int_ewa_40',
       'Performance_Blocks_ewa_40', 'Expected_xG_ewa_40',
       'Expected_npxG_ewa_40', 'Expected_xA_ewa_40', 'SCA_SCA_ewa_40',
       'Passes_Cmp_ewa_40', 'Passes_Cmp%_ewa_40', 'Passes_Prog_ewa_40',
       'Carries_Carries_ewa_40', 'Carries_Prog_ewa_40',
       'Dribbles_Succ_ewa_40', 'Dribbles_Att_ewa_40', 'General_KP_ewa_40',
       'Touches_Att 3rd_ewa_40', 'Touches_Att Pen_ewa_40',
       'Performance_Recov_ewa_40', 'Aerial Duels_Won_ewa_40',
       'Aerial Duels_Won%_ewa_40', 'fbref_position_GK_ewa5',
       'fbref_position_LB_ewa5', 'fbref_position_CB_ewa5',
       'fbref_position_RB_ewa5', 'fbref_position_WB_ewa5',
       'fbref_position_DM_ewa5', 'fbref_position_LM_ewa5',
       'fbref_position_CM_ewa5', 'fbref_position_RM_ewa5',
       'fbref_position_AM_ewa5', 'fbref_position_LW_ewa5',
       'fbref_position_RW_ewa5', 'fbref_position_FW_ewa5',
       'fbref_position_GK_ewa10', 'fbref_position_LB_ewa10',
       'fbref_position_CB_ewa10', 'fbref_position_RB_ewa10',
       'fbref_position_WB_ewa10', 'fbref_position_DM_ewa10',
       'fbref_position_LM_ewa10', 'fbref_position_CM_ewa10',
       'fbref_position_RM_ewa10', 'fbref_position_AM_ewa10',
       'fbref_position_LW_ewa10', 'fbref_position_RW_ewa10',
       'fbref_position_FW_ewa10', 'fbref_position_GK_ewa20',
       'fbref_position_LB_ewa20', 'fbref_position_CB_ewa20',
       'fbref_position_RB_ewa20', 'fbref_position_WB_ewa20',
       'fbref_position_DM_ewa20', 'fbref_position_LM_ewa20',
       'fbref_position_CM_ewa20', 'fbref_position_RM_ewa20',
       'fbref_position_AM_ewa20', 'fbref_position_LW_ewa20',
       'fbref_position_RW_ewa20', 'fbref_position_FW_ewa20',
       'fbref_position_GK_ewa40', 'fbref_position_LB_ewa40',
       'fbref_position_CB_ewa40', 'fbref_position_RB_ewa40',
       'fbref_position_WB_ewa40', 'fbref_position_DM_ewa40',
       'fbref_position_LM_ewa40', 'fbref_position_CM_ewa40',
       'fbref_position_RM_ewa40', 'fbref_position_AM_ewa40',
       'fbref_position_LW_ewa40', 'fbref_position_RW_ewa40',
       'fbref_position_FW_ewa40',
       ]
keep = [target] + input_variables

training = training_full[keep].copy()
validation = validation_full[keep].copy()
testing = testing_full[keep].copy()
display(training)
display(validation)
display(testing)

total_points  fpl_position_GK  fpl_position_DEF  fpl_position_MID  \
0                 0              0.0               1.0               0.0   
1752              1              0.0               1.0               0.0   
3513              1              0.0               1.0               0.0   
5141              6              0.0               1.0               0.0   
5295              9              0.0               1.0               0.0   
...             ...              ...               ...               ...   
21549             2              0.0               1.0               0.0   
21597            12              0.0               1.0               0.0   
21845             1              0.0               1.0               0.0   
22088             2              0.0               1.0               0.0   
22072             1              0.0               1.0               0.0   

       fpl_position_FWD  fbref_position_GK  fbref_position_LB  \
0                   0.0                  0                  1   
1752                0.0                  0                  1   
3513                0.0                  0                  1   
5141                0.0                  0                  0   
5295                0.0                  0                  0   
...                 ...                ...                ...   
21549               0.0                  0                  1   
21597               0.0                  0                  0   
21845               0.0                  0                  0   
22088               0.0                  0                  0   
22072               0.0                  0                  0   

       fbref_position_CB  fbref_position_RB  fbref_position_WB  \
0                      0                  0                  0   
1752                   0                  0                  0   
3513                   0                  0                  0   
5141                   0                  0                  1   
5295                   0                  0                  1   
...                  ...                ...                ...   
21549                  0                  0                  0   
21597                  0                  0                  1   
21845                  0                  0                  1   
22088                  0                  0                  1   
22072                  1                  0                  0   

       fbref_position_DM  fbref_position_LM  fbref_position_CM  \
0                      0                  0                  0   
1752                   0                  0                  0   
3513                   0                  0                  0   
5141                   0                  0                  0   
5295                   0                  0                  0   
...                  ...                ...                ...   
21549                  0                  0                  0   
21597                  0                  0                  0   
21845                  0                  0                  0   
22088                  0                  0                  0   
22072                  0                  0                  0   

       fbref_position_RM  fbref_position_AM  fbref_position_LW  \
0                      0                  0                  0   
1752                   0                  0                  0   
3513                   0                  0                  0   
5141                   0                  0                  0   
5295                   0                  0                  0   
...                  ...                ...                ...   
21549                  0                  0                  0   
21597                  0                  0                  0   
21845                  0                  0                  0   
22088                  0                  0                  0   
2

total_points  fpl_position_GK  fpl_position_DEF  fpl_position_MID  \
22189             1              0.0               1.0               0.0   
22390             1              0.0               1.0               0.0   
22642             7              0.0               1.0               0.0   
22889            15              0.0               1.0               0.0   
23137             5              0.0               1.0               0.0   
...             ...              ...               ...               ...   
31594             7              0.0               1.0               0.0   
31456             1              0.0               0.0               1.0   
31714             1              0.0               0.0               1.0   
31510             1              0.0               0.0               1.0   
31530             1              0.0               0.0               1.0   

       fpl_position_FWD  fbref_position_GK  fbref_position_LB  \
22189               0.0                  0                  1   
22390               0.0                  0                  1   
22642               0.0                  0                  0   
22889               0.0                  0                  0   
23137               0.0                  0                  0   
...                 ...                ...                ...   
31594               0.0                  0                  0   
31456               0.0                  0                  0   
31714               0.0                  0                  0   
31510               0.0                  0                  0   
31530               0.0                  0                  0   

       fbref_position_CB  fbref_position_RB  fbref_position_WB  \
22189                  0                  0                  0   
22390                  1                  0                  0   
22642                  1                  0                  0   
22889                  1                  0                  0   
23137                  1                  0                  0   
...                  ...                ...                ...   
31594                  1                  0                  0   
31456                  0                  0                  0   
31714                  0                  0                  0   
31510                  0                  0                  0   
31530                  0                  0                  1   

       fbref_position_DM  fbref_position_LM  fbref_position_CM  \
22189                  0                  0                  0   
22390                  0                  0                  0   
22642                  0                  0                  0   
22889                  0                  0                  0   
23137                  0                  0                  0   
...                  ...                ...                ...   
31594                  0                  0                  0   
31456                  0                  0                  1   
31714                  0                  0                  0   
31510                  0                  0                  1   
31530                  0                  0                  0   

       fbref_position_RM  fbref_position_AM  fbref_position_LW  \
22189                  0                  0                  0   
22390                  0                  0                  0   
22642                  0                  0                  0   
22889                  0                  0                  0   
23137                  0                  0                  0   
...                  ...                ...                ...   
31594                  0                  0                  0   
31456                  0                  0                  0   
31714                  0                  0                  0   
31510                  0                  1                  0   
3

total_points  fpl_position_GK  fpl_position_DEF  fpl_position_MID  \
31978             7              0.0               1.0               0.0   
32236             2              0.0               1.0               0.0   
32489             5              0.0               1.0               0.0   
32747             8              0.0               1.0               0.0   
33003             1              0.0               1.0               0.0   
...             ...              ...               ...               ...   
40554             1              0.0               0.0               1.0   
40555             2              0.0               0.0               1.0   
40921             0              0.0               0.0               1.0   
40851             1              0.0               0.0               0.0   
40970             1              0.0               0.0               1.0   

       fpl_position_FWD  fbref_position_GK  fbref_position_LB  \
31978               0.0                  0                  1   
32236               0.0                  0                  1   
32489               0.0                  0                  1   
32747               0.0                  0                  1   
33003               0.0                  0                  1   
...                 ...                ...                ...   
40554               0.0                  0                  0   
40555               0.0                  0                  0   
40921               0.0                  0                  0   
40851               1.0                  0                  0   
40970               0.0                  0                  0   

       fbref_position_CB  fbref_position_RB  fbref_position_WB  \
31978                  1                  0                  0   
32236                  0                  0                  0   
32489                  0                  0                  0   
32747                  0                  0                  0   
33003                  0                  0                  0   
...                  ...                ...                ...   
40554                  0                  0                  0   
40555                  0                  0                  0   
40921                  0                  0                  0   
40851                  0                  0                  0   
40970                  0                  0                  0   

       fbref_position_DM  fbref_position_LM  fbref_position_CM  \
31978                  0                  0                  0   
32236                  0                  0                  0   
32489                  0                  0                  0   
32747                  0                  0                  0   
33003                  0                  0                  0   
...                  ...                ...                ...   
40554                  0                  0                  0   
40555                  0                  0                  0   
40921                  0                  0                  0   
40851                  0                  0                  0   
40970                  1                  0                  0   

       fbref_position_RM  fbref_position_AM  fbref_position_LW  \
31978                  0                  0                  0   
32236                  0                  0                  0   
32489                  0                  0                  0   
32747                  0                  0                  0   
33003                  0                  0                  0   
...                  ...                ...                ...   
40554                  0                  0                  1   
40555                  1                  0                  0   
40921                  0                  0                  0   
40851                  0                  0                  0   
4

In [9]:
training_X = training[input_variables].copy()
training_y = training[target].copy()
validation_X = validation[input_variables].copy()
validation_y = validation[target].copy()
testing_X = testing[input_variables].copy()
testing_y = testing[target].copy()

print('training_X:')
display(training_X)
print('training_y:')
display(training_y)

training_X:


fpl_position_GK  fpl_position_DEF  fpl_position_MID  fpl_position_FWD  \
0                  0.0               1.0               0.0               0.0   
1752               0.0               1.0               0.0               0.0   
3513               0.0               1.0               0.0               0.0   
5141               0.0               1.0               0.0               0.0   
5295               0.0               1.0               0.0               0.0   
...                ...               ...               ...               ...   
21549              0.0               1.0               0.0               0.0   
21597              0.0               1.0               0.0               0.0   
21845              0.0               1.0               0.0               0.0   
22088              0.0               1.0               0.0               0.0   
22072              0.0               1.0               0.0               0.0   

       fbref_position_GK  fbref_position_LB  fbref_position_CB  \
0                      0                  1                  0   
1752                   0                  1                  0   
3513                   0                  1                  0   
5141                   0                  0                  0   
5295                   0                  0                  0   
...                  ...                ...                ...   
21549                  0                  1                  0   
21597                  0                  0                  0   
21845                  0                  0                  0   
22088                  0                  0                  0   
22072                  0                  0                  1   

       fbref_position_RB  fbref_position_WB  fbref_position_DM  \
0                      0                  0                  0   
1752                   0                  0                  0   
3513                   0                  0                  0   
5141                   0                  1                  0   
5295                   0                  1                  0   
...                  ...                ...                ...   
21549                  0                  0                  0   
21597                  0                  1                  0   
21845                  0                  1                  0   
22088                  0                  1                  0   
22072                  0                  0                  0   

       fbref_position_LM  fbref_position_CM  fbref_position_RM  \
0                      0                  0                  0   
1752                   0                  0                  0   
3513                   0                  0                  0   
5141                   0                  0                  0   
5295                   0                  0                  0   
...                  ...                ...                ...   
21549                  0                  0                  0   
21597                  0                  0                  0   
21845                  0                  0                  0   
22088                  0                  0                  0   
22072                  0                  0                  0   

       fbref_position_AM  fbref_position_LW  fbref_position_RW  \
0                      0                  0                  0   
1752                   0                  0                  0   
3513                   0                  0                  0   
5141                   0                  0                  0   
5295                   0                  0                  0   
...                  ...                ...                ...   
21549                  0                  0                  0   
21597                  0                  0                  0   
21845                  0                  0                  0   
22088  

training_y:


0         0
1752      1
3513      1
5141      6
5295      9
         ..
21549     2
21597    12
21845     1
22088     2
22072     1
Name: total_points, Length: 22084, dtype: int64

# MODELLING

## Monotone constraints

In [32]:
def objective(trial):
    
    # parameters
    xgb_params = {}
    xgb_params['learning_rate'] = trial.suggest_float('learning_rate', 0.001, 1)
    xgb_params['max_depth'] = trial.suggest_int('max_depth',2,10)
    xgb_params['min_child_weight'] = trial.suggest_float('min_child_weight', 0.01, 2)
    xgb_params['gamma'] = trial.suggest_float('gamma', 0, 0.5)
    xgb_params['subsample'] = trial.suggest_float('subsample', 0.5, 1)
    xgb_params['colsample_bytree'] = trial.suggest_float('colsample_bytree', 0.5, 1)
    xgb_params['n_estimators'] = 200
    xgb_params['monotone_constraints'] = monotone_constraints

    fit_params = {}
    fit_params['early_stopping_rounds'] = 25
    #fit_params['sample_weight'] = 
    #fit_params['sample_weight_eval_set'] = 
    
    # train model
    model = XGBRegressor(**xgb_params)
    model.fit(training_X, training_y, eval_set=[(validation_X, validation_y)], 
              early_stopping_rounds = fit_params['early_stopping_rounds'],)
    # get rmse of the model on the test set
    predictions = model.predict(validation_X)
    rmse = mean_squared_error(validation_y, predictions, squared=False)
    
    return rmse

In [15]:
input_variables

['fpl_position_GK',
 'fpl_position_DEF',
 'fpl_position_MID',
 'fpl_position_FWD',
 'fbref_position_GK',
 'fbref_position_LB',
 'fbref_position_CB',
 'fbref_position_RB',
 'fbref_position_WB',
 'fbref_position_DM',
 'fbref_position_LM',
 'fbref_position_CM',
 'fbref_position_RM',
 'fbref_position_AM',
 'fbref_position_LW',
 'fbref_position_RW',
 'fbref_position_FW',
 'team_xG_ewa_5_shifted',
 'team_xG_ewa_10_shifted',
 'team_xG_ewa_20_shifted',
 'team_xG_ewa_40_shifted',
 'team_xGA_ewa_5_shifted',
 'team_xGA_ewa_10_shifted',
 'team_xGA_ewa_20_shifted',
 'team_xGA_ewa_40_shifted',
 'opp_team_xG_ewa_5_shifted',
 'opp_team_xG_ewa_10_shifted',
 'opp_team_xG_ewa_20_shifted',
 'opp_team_xG_ewa_40_shifted',
 'opp_team_xGA_ewa_5_shifted',
 'opp_team_xGA_ewa_10_shifted',
 'opp_team_xGA_ewa_20_shifted',
 'opp_team_xGA_ewa_40_shifted',
 'games_in_past_5_days',
 'games_in_past_10_days',
 'games_in_past_20_days',
 'games_in_past_40_days',
 'transfers_balance_%',
 'transfers_balance_%_ewa5',
 'trans

In [31]:
monotone_constraints = {}

monotone_constraints['opp_team_xG_ewa_5_shifted'] = -1
monotone_constraints['opp_team_xG_ewa_10_shifted'] = -1
monotone_constraints['opp_team_xG_ewa_20_shifted'] = -1
monotone_constraints['opp_team_xG_ewa_40_shifted'] = -1

monotone_constraints['opp_team_xGA_ewa_5_shifted'] = 1
monotone_constraints['opp_team_xGA_ewa_10_shifted'] = 1
monotone_constraints['opp_team_xGA_ewa_20_shifted'] = 1
monotone_constraints['opp_team_xGA_ewa_40_shifted'] = 1

monotone_constraints['bps_ewa_5'] = 1
monotone_constraints['bps_ewa_10'] = 1
monotone_constraints['bps_ewa_20'] = 1
monotone_constraints['bps_ewa_40'] = 1

monotone_constraints['xPoints_ewa_5'] = 1
monotone_constraints['xPoints_ewa_10'] = 1
monotone_constraints['xPoints_ewa_20'] = 1
monotone_constraints['xPoints_ewa_40'] = 1

monotone_constraints['Expected_xG_ewa_5'] = 1
monotone_constraints['Expected_xG_ewa_10'] = 1
monotone_constraints['Expected_xG_ewa_20'] = 1
monotone_constraints['Expected_xG_ewa_40'] = 1

monotone_constraints['Expected_xA_ewa_5'] = 1
monotone_constraints['Expected_xA_ewa_10'] = 1
monotone_constraints['Expected_xA_ewa_20'] = 1
monotone_constraints['Expected_xA_ewa_40'] = 1

monotone_constraints 

{'opp_team_xG_ewa_5_shifted': -1,
 'opp_team_xG_ewa_10_shifted': -1,
 'opp_team_xG_ewa_20_shifted': -1,
 'opp_team_xG_ewa_40_shifted': -1,
 'opp_team_xGA_ewa_5_shifted': 1,
 'opp_team_xGA_ewa_10_shifted': 1,
 'opp_team_xGA_ewa_20_shifted': 1,
 'opp_team_xGA_ewa_40_shifted': 1,
 'bps_ewa_5': 1,
 'bps_ewa_10': 1,
 'bps_ewa_20': 1,
 'bps_ewa_40': 1,
 'xPoints_ewa_5': 1,
 'xPoints_ewa_10': 1,
 'xPoints_ewa_20': 1,
 'xPoints_ewa_40': 1,
 'Expected_xG_ewa_5': 1,
 'Expected_xG_ewa_10': 1,
 'Expected_xG_ewa_20': 1,
 'Expected_xG_ewa_40': 1,
 'Expected_xA_ewa_5': 1,
 'Expected_xA_ewa_10': 1,
 'Expected_xA_ewa_20': 1,
 'Expected_xA_ewa_40': 1}

In [33]:
optimize(200, training_X, training_y, validation_X, validation_y)

[I 2022-07-26 21:39:29,016] A new study created in memory with name: no-name-5c483f33-93d2-4429-8892-2789f5e3c724
/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning: pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  elif isinstance(data.columns, (pd.Int64Index, pd.RangeIndex)):


[0]	validation_0-rmse:3.24579
[1]	validation_0-rmse:3.02218
[2]	validation_0-rmse:2.96210
[3]	validation_0-rmse:2.96511
[4]	validation_0-rmse:2.96605
[5]	validation_0-rmse:2.97459
[6]	validation_0-rmse:2.98384
[7]	validation_0-rmse:2.99023
[8]	validation_0-rmse:3.00236
[9]	validation_0-rmse:3.01351
[10]	validation_0-rmse:3.01820
[11]	validation_0-rmse:3.02616
[12]	validation_0-rmse:3.03288
[13]	validation_0-rmse:3.03993
[14]	validation_0-rmse:3.05147
[15]	validation_0-rmse:3.05397
[16]	validation_0-rmse:3.05755
[17]	validation_0-rmse:3.06543
[18]	validation_0-rmse:3.08084
[19]	validation_0-rmse:3.09148
[20]	validation_0-rmse:3.09741
[21]	validation_0-rmse:3.10457
[22]	validation_0-rmse:3.10655
[23]	validation_0-rmse:3.12309
[24]	validation_0-rmse:3.13087
[25]	validation_0-rmse:3.14062
[26]	validation_0-rmse:3.15053
[27]	validation_0-rmse:3.15799


[I 2022-07-26 21:39:36,302] Trial 0 finished with value: 2.962098203363639 and parameters: {'learning_rate': 0.48534775298321137, 'max_depth': 8, 'min_child_weight': 1.77216059092639, 'gamma': 0.46487948109095856, 'subsample': 0.8144355436265942, 'colsample_bytree': 0.8471857790935096}. Best is trial 0 with value: 2.962098203363639.


[0]	validation_0-rmse:3.21612


/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning: pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  elif isinstance(data.columns, (pd.Int64Index, pd.RangeIndex)):


...

[0]	validation_0-rmse:3.86178
[1]	validation_0-rmse:3.75046
[2]	validation_0-rmse:3.65391
[3]	validation_0-rmse:3.56752
[4]	validation_0-rmse:3.48902
[5]	validation_0-rmse:3.41969
[6]	validation_0-rmse:3.35752
[7]	validation_0-rmse:3.30280
[8]	validation_0-rmse:3.25617
[9]	validation_0-rmse:3.21302
[10]	validation_0-rmse:3.17651
[11]	validation_0-rmse:3.14273
[12]	validation_0-rmse:3.11396
[13]	validation_0-rmse:3.08960
[14]	validation_0-rmse:3.06722
[15]	validation_0-rmse:3.04792
[16]	validation_0-rmse:3.03089
[17]	validation_0-rmse:3.01673
[18]	validation_0-rmse:3.00416
[19]	validation_0-rmse:2.99321
[20]	validation_0-rmse:2.98318
[21]	validation_0-rmse:2.97402
[22]	validation_0-rmse:2.96608
[23]	validation_0-rmse:2.95846
[24]	validation_0-rmse:2.95269
[25]	validation_0-rmse:2.94716
[26]	validation_0-rmse:2.94251
[27]	validation_0-rmse:2.93831
[28]	validation_0-rmse:2.93499
[29]	validation_0-rmse:2.93224
[30]	validation_0-rmse:2.92935
[31]	validation_0-rmse:2.92690
[32]	validation_0-

[I 2022-07-26 22:05:43,625] Trial 198 finished with value: 2.9081371354623182 and parameters: {'learning_rate': 0.06946645370281203, 'max_depth': 3, 'min_child_weight': 0.899784682940698, 'gamma': 0.21532694061722307, 'subsample': 0.9247370961814517, 'colsample_bytree': 0.9152356442656526}. Best is trial 21 with value: 2.9036373008283727.
/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning: pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  elif isinstance(data.columns, (pd.Int64Index, pd.RangeIndex)):


[0]	validation_0-rmse:3.91427
[1]	validation_0-rmse:3.84427
[2]	validation_0-rmse:3.77925
[3]	validation_0-rmse:3.71693
[4]	validation_0-rmse:3.65977
[5]	validation_0-rmse:3.60618
[6]	validation_0-rmse:3.55682
[7]	validation_0-rmse:3.51081
[8]	validation_0-rmse:3.46801
[9]	validation_0-rmse:3.42804
[10]	validation_0-rmse:3.38756
[11]	validation_0-rmse:3.35236
[12]	validation_0-rmse:3.32093
[13]	validation_0-rmse:3.29063
[14]	validation_0-rmse:3.26318
[15]	validation_0-rmse:3.23756
[16]	validation_0-rmse:3.21439
[17]	validation_0-rmse:3.19152
[18]	validation_0-rmse:3.17137
[19]	validation_0-rmse:3.15173
[20]	validation_0-rmse:3.13409
[21]	validation_0-rmse:3.11725
[22]	validation_0-rmse:3.10103
[23]	validation_0-rmse:3.08650
[24]	validation_0-rmse:3.07300
[25]	validation_0-rmse:3.05985
[26]	validation_0-rmse:3.04883
[27]	validation_0-rmse:3.03845
[28]	validation_0-rmse:3.02836
[29]	validation_0-rmse:3.01936
[30]	validation_0-rmse:3.01083
[31]	validation_0-rmse:3.00307
[32]	validation_0-

[I 2022-07-26 22:05:57,307] Trial 199 finished with value: 2.9128520861245892 and parameters: {'learning_rate': 0.04096711269538596, 'max_depth': 4, 'min_child_weight': 0.814094809635061, 'gamma': 0.05027243608532847, 'subsample': 0.5325548057002593, 'colsample_bytree': 0.7766625220717503}. Best is trial 21 with value: 2.9036373008283727.


Best params:
{'learning_rate': 0.16359329064327055, 'max_depth': 3, 'min_child_weight': 0.8842811259605042, 'gamma': 0.33111046011862855, 'subsample': 0.937714592257693, 'colsample_bytree': 0.777931690188467}
RMSE for best params:
2.9036373008283727


In [37]:
xgb_params = {}
xgb_params['learning_rate'] = 0.164
xgb_params['max_depth'] = 3
xgb_params['min_child_weight'] = 0.884
xgb_params['gamma'] = 0.331
xgb_params['subsample'] = 0.938
xgb_params['colsample_bytree'] = 0.778
xgb_params['n_estimators'] = 200
xgb_params['monotone_constraints'] = monotone_constraints

fit_early_stopping_rounds = 25

model = train_model(xgb_params, fit_early_stopping_rounds, training_X, training_y, validation_X, validation_y)

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning: pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  elif isinstance(data.columns, (pd.Int64Index, pd.RangeIndex)):


[0]	validation_0-rmse:3.69959
[1]	validation_0-rmse:3.48595
[2]	validation_0-rmse:3.33109
[3]	validation_0-rmse:3.21390
[4]	validation_0-rmse:3.12863
[5]	validation_0-rmse:3.06679
[6]	validation_0-rmse:3.02290
[7]	validation_0-rmse:2.99163
[8]	validation_0-rmse:2.96969
[9]	validation_0-rmse:2.95290
[10]	validation_0-rmse:2.94162
[11]	validation_0-rmse:2.93237
[12]	validation_0-rmse:2.92393
[13]	validation_0-rmse:2.91877
[14]	validation_0-rmse:2.91535
[15]	validation_0-rmse:2.91430
[16]	validation_0-rmse:2.91232
[17]	validation_0-rmse:2.91112
[18]	validation_0-rmse:2.90965
[19]	validation_0-rmse:2.90858
[20]	validation_0-rmse:2.90762
[21]	validation_0-rmse:2.90786
[22]	validation_0-rmse:2.90738
[23]	validation_0-rmse:2.90633
[24]	validation_0-rmse:2.90593
[25]	validation_0-rmse:2.90520
[26]	validation_0-rmse:2.90444
[27]	validation_0-rmse:2.90467
[28]	validation_0-rmse:2.90437
[29]	validation_0-rmse:2.90455
[30]	validation_0-rmse:2.90424
[31]	validation_0-rmse:2.90386
[32]	validation_0-

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning: pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  elif isinstance(data.columns, (pd.Int64Index, pd.RangeIndex)):


In [39]:
draw_player_predictions('Kane', testing_full, model)

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.



Total true points: 185
Total expected points: 194.42233788147274
Total predicted points: 199.84268188476562


In [43]:
stats_df = calculate_all_player_predictions(testing_full, model)

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/

...

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/

In [44]:
draw_all_predictions(stats_df)

## sample_weights

In [60]:
def objective(trial):
    
    # parameters
    xgb_params = {}
    xgb_params['learning_rate'] = trial.suggest_float('learning_rate', 0.001, 1)
    xgb_params['max_depth'] = trial.suggest_int('max_depth',2,10)
    xgb_params['min_child_weight'] = trial.suggest_float('min_child_weight', 0.01, 2)
    xgb_params['gamma'] = trial.suggest_float('gamma', 0, 0.5)
    xgb_params['subsample'] = trial.suggest_float('subsample', 0.5, 1)
    xgb_params['colsample_bytree'] = trial.suggest_float('colsample_bytree', 0.5, 1)
    xgb_params['n_estimators'] = 200
    #xgb_params['monotone_constraints'] = monotone_constraints

    fit_params = {}
    fit_params['early_stopping_rounds'] = 25
    sample_weight = training_X['xPoints_ewa_40'].fillna(1)
    sample_weight[sample_weight<1] = 1
    fit_params['sample_weight'] = sample_weight
    sample_weight_eval_set = validation_X['xPoints_ewa_40'].fillna(1)
    sample_weight_eval_set[sample_weight_eval_set<1] = 1
    fit_params['sample_weight_eval_set'] = [sample_weight_eval_set]
    
    # train model
    model = XGBRegressor(**xgb_params)
    model.fit(training_X, training_y, eval_set=[(validation_X, validation_y)], **fit_params)
    # get rmse of the model on the test set
    predictions = model.predict(validation_X)
    rmse = mean_squared_error(validation_y, predictions, squared=False)
    
    return rmse

In [61]:
optimize(200, training_X, training_y, validation_X, validation_y)

[I 2022-07-27 12:16:18,871] A new study created in memory with name: no-name-06fe6298-a9ab-45ce-bfb4-214940e6fee9
/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.



[0]	validation_0-rmse:3.28853
[1]	validation_0-rmse:3.14197
[2]	validation_0-rmse:3.12762
[3]	validation_0-rmse:3.13501
[4]	validation_0-rmse:3.14769
[5]	validation_0-rmse:3.14910
[6]	validation_0-rmse:3.14990
[7]	validation_0-rmse:3.16695
[8]	validation_0-rmse:3.17112
[9]	validation_0-rmse:3.18502
[10]	validation_0-rmse:3.19668
[11]	validation_0-rmse:3.20207
[12]	validation_0-rmse:3.21197
[13]	validation_0-rmse:3.22199
[14]	validation_0-rmse:3.24344
[15]	validation_0-rmse:3.25222
[16]	validation_0-rmse:3.24892
[17]	validation_0-rmse:3.26026
[18]	validation_0-rmse:3.26593
[19]	validation_0-rmse:3.26931
[20]	validation_0-rmse:3.28652
[21]	validation_0-rmse:3.29749
[22]	validation_0-rmse:3.29607
[23]	validation_0-rmse:3.30775
[24]	validation_0-rmse:3.33968
[25]	validation_0-rmse:3.35438
[26]	validation_0-rmse:3.36404
[27]	validation_0-rmse:3.37344


[I 2022-07-27 12:16:21,592] Trial 0 finished with value: 2.9470564067447493 and parameters: {'learning_rate': 0.6515363233278348, 'max_depth': 4, 'min_child_weight': 0.15997356681497021, 'gamma': 0.05942914254211301, 'subsample': 0.5497703790951844, 'colsample_bytree': 0.7420718862246274}. Best is trial 0 with value: 2.9470564067447493.
/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.



[0]	validation_0-rmse:3.49675
[1]	validation_0-rmse:3.30318
[2]	validation_0-rmse:3.26291
[3]	validation_0-rmse:3.28355
[4]	validation_0-rmse:3.29094
[5]	validation_0-rmse:3.30569
[6]	validation_0-rmse:3.31644
[7]	validation_0-rmse:3.34339
[8]	validation_0-rmse:3.35810
[9]	validation_0-rmse:3.36894
[10]	validation_0-rmse:3.38096
[11]	validation_0-rmse:3.39949
[12]	validation_0-rmse:3.41088
[13]	validation_0-rmse:3.43823
[14]	validation_0-rmse:3.44678
[15]	validation_0-rmse:3.46335
[16]	validation_0-rmse:3.47552
[17]	validation_0-rmse:3.49407
[18]	validation_0-rmse:3.49550
[19]	validation_0-rmse:3.49734
[20]	validation_0-rmse:3.51929
[21]	validation_0-rmse:3.52979
[22]	validation_0-rmse:3.54474
[23]	validation_0-rmse:3.55508
[24]	validation_0-rmse:3.56882
[25]	validation_0-rmse:3.57640
[26]	validation_0-rmse:3.58713
[27]	validation_0-rmse:3.59425


[I 2022-07-27 12:16:27,082] Trial 1 finished with value: 3.058806291222856 and parameters: {'learning_rate': 0.49241309240242603, 'max_depth': 8, 'min_child_weight': 1.0585812695494707, 'gamma': 0.17383493665767968, 'subsample': 0.7410001454641608, 'colsample_bytree': 0.6697736855090497}. Best is trial 0 with value: 2.9470564067447493.
/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.



...

[0]	validation_0-rmse:4.18584
[1]	validation_0-rmse:4.09963
[2]	validation_0-rmse:4.01949
[3]	validation_0-rmse:3.94655
[4]	validation_0-rmse:3.87776
[5]	validation_0-rmse:3.81389
[6]	validation_0-rmse:3.75468
[7]	validation_0-rmse:3.70083
[8]	validation_0-rmse:3.65179
[9]	validation_0-rmse:3.60432
[10]	validation_0-rmse:3.56136
[11]	validation_0-rmse:3.52222
[12]	validation_0-rmse:3.48503
[13]	validation_0-rmse:3.45175
[14]	validation_0-rmse:3.42137
[15]	validation_0-rmse:3.39242
[16]	validation_0-rmse:3.36652
[17]	validation_0-rmse:3.34204
[18]	validation_0-rmse:3.32081
[19]	validation_0-rmse:3.30001
[20]	validation_0-rmse:3.28118
[21]	validation_0-rmse:3.26432
[22]	validation_0-rmse:3.24931
[23]	validation_0-rmse:3.23435
[24]	validation_0-rmse:3.22146
[25]	validation_0-rmse:3.20958
[26]	validation_0-rmse:3.19823
[27]	validation_0-rmse:3.18836
[28]	validation_0-rmse:3.17941
[29]	validation_0-rmse:3.17040
[30]	validation_0-rmse:3.16266
[31]	validation_0-rmse:3.15646
[32]	validation_0-

[I 2022-07-27 12:48:42,442] Trial 198 finished with value: 2.909554614069152 and parameters: {'learning_rate': 0.04656493757108791, 'max_depth': 3, 'min_child_weight': 0.07435510763990717, 'gamma': 0.1901597780488623, 'subsample': 0.9564420551486701, 'colsample_bytree': 0.8631306784047003}. Best is trial 147 with value: 2.9066224972784305.
/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.



[0]	validation_0-rmse:4.27619
[1]	validation_0-rmse:4.27279
[2]	validation_0-rmse:4.26940
[3]	validation_0-rmse:4.26604
[4]	validation_0-rmse:4.26267
[5]	validation_0-rmse:4.25932
[6]	validation_0-rmse:4.25600
[7]	validation_0-rmse:4.25265
[8]	validation_0-rmse:4.24932
[9]	validation_0-rmse:4.24601
[10]	validation_0-rmse:4.24268
[11]	validation_0-rmse:4.23938
[12]	validation_0-rmse:4.23616
[13]	validation_0-rmse:4.23287
[14]	validation_0-rmse:4.22959
[15]	validation_0-rmse:4.22630
[16]	validation_0-rmse:4.22303
[17]	validation_0-rmse:4.21978
[18]	validation_0-rmse:4.21652
[19]	validation_0-rmse:4.21327
[20]	validation_0-rmse:4.21005
[21]	validation_0-rmse:4.20683
[22]	validation_0-rmse:4.20369
[23]	validation_0-rmse:4.20047
[24]	validation_0-rmse:4.19728
[25]	validation_0-rmse:4.19409
[26]	validation_0-rmse:4.19089
[27]	validation_0-rmse:4.18776
[28]	validation_0-rmse:4.18467
[29]	validation_0-rmse:4.18150
[30]	validation_0-rmse:4.17836
[31]	validation_0-rmse:4.17524
[32]	validation_0-

[I 2022-07-27 12:49:03,509] Trial 199 finished with value: 3.512822963169949 and parameters: {'learning_rate': 0.001669956116998536, 'max_depth': 3, 'min_child_weight': 0.13567314326999685, 'gamma': 0.16662558480655087, 'subsample': 0.9996125119038766, 'colsample_bytree': 0.9100008944710166}. Best is trial 147 with value: 2.9066224972784305.


Best params:
{'learning_rate': 0.04374952248431104, 'max_depth': 3, 'min_child_weight': 0.6574966399161046, 'gamma': 0.12052244570807029, 'subsample': 0.9685013879981486, 'colsample_bytree': 0.8754667751686543}
RMSE for best params:
2.9066224972784305


In [64]:
# parameters
xgb_params = {}
xgb_params['learning_rate'] = 0.044
xgb_params['max_depth'] = 3
xgb_params['min_child_weight'] = 0.657
xgb_params['gamma'] = 0.121
xgb_params['subsample'] = 0.969
xgb_params['colsample_bytree'] = 0.875
xgb_params['n_estimators'] = 200

fit_params = {}
fit_params['early_stopping_rounds'] = 25
sample_weight = training_X['xPoints_ewa_40'].fillna(1)
sample_weight[sample_weight<1] = 1
fit_params['sample_weight'] = sample_weight
sample_weight_eval_set = validation_X['xPoints_ewa_40'].fillna(1)
sample_weight_eval_set[sample_weight_eval_set<1] = 1
fit_params['sample_weight_eval_set'] = [sample_weight_eval_set]

model = train_model(xgb_params, fit_params, training_X, training_y, validation_X, validation_y, testing_X, testing_y)

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.



[0]	validation_0-rmse:4.19101
[1]	validation_0-rmse:4.10916
[2]	validation_0-rmse:4.03373
[3]	validation_0-rmse:3.96232
[4]	validation_0-rmse:3.89640
[5]	validation_0-rmse:3.83434
[6]	validation_0-rmse:3.77655
[7]	validation_0-rmse:3.72390
[8]	validation_0-rmse:3.67501
[9]	validation_0-rmse:3.62810
[10]	validation_0-rmse:3.58527
[11]	validation_0-rmse:3.54543
[12]	validation_0-rmse:3.50831
[13]	validation_0-rmse:3.47521
[14]	validation_0-rmse:3.44450
[15]	validation_0-rmse:3.41603
[16]	validation_0-rmse:3.39002
[17]	validation_0-rmse:3.36523
[18]	validation_0-rmse:3.34200
[19]	validation_0-rmse:3.32106
[20]	validation_0-rmse:3.30086
[21]	validation_0-rmse:3.28420
[22]	validation_0-rmse:3.26809
[23]	validation_0-rmse:3.25296
[24]	validation_0-rmse:3.23917
[25]	validation_0-rmse:3.22682
[26]	validation_0-rmse:3.21499
[27]	validation_0-rmse:3.20321
[28]	validation_0-rmse:3.19369
[29]	validation_0-rmse:3.18416
[30]	validation_0-rmse:3.17572
[31]	validation_0-rmse:3.16846
[32]	validation_0-

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.



In [67]:
draw_player_predictions('Heung', testing_full, model)

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.



Total true points: 255
Total expected points: 212.38199498231182
Total predicted points: 168.83688354492188


In [70]:
stats_df = calculate_all_player_predictions(testing_full, model)

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/

...

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning:

pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.

/Users/jaakkotoivonen/opt/anaconda3/lib/

In [71]:
draw_all_predictions(stats_df)